In [2]:
import json
import pandas as pd
from twitter import *
from numpy import random
import json

import tweepy
from tweepy import OAuthHandler
from tweepy import Cursor
import os
import json
import pandas as pd

In [3]:
#Collect Data 
#Variables that contains the user credentials to access Twitter API
consumer_key = "88bk52CBiM5shvQ7xOwMtilYX" #API key
consumer_secret = "ngSSPufrYS08XcbvrNn2Jwagz7O6MWk0VMEv9j00SpyzYatIbU"
access_token = "1196669881841668097-RYta5RN917fQgOd8LbMR2FENeFNsSl"
access_token_secret = "mpjlkqpsVk0iexxFjuK64XGGOf0hv5QxX499mfYpPghY1"

auth = OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_token, access_token_secret)
api = tweepy.API(auth,wait_on_rate_limit=True,wait_on_rate_limit_notify=True)

In [4]:
def getUserAttributes(screen_name):
    user = api.get_user(screen_name)
    print("Screen name: ", user.screen_name)
    print("Number of Followers: ", user.followers_count)
    print("Number of Friends: ", user.friends_count)
getUserAttributes("adidas")

Screen name:  adidas
Number of Followers:  3866756
Number of Friends:  160


In [121]:
def getUserProfiles(screen_name):
    dirname = "output/users/{}".format(screen_name)
    os.makedirs(dirname, mode=0o755, exist_ok=True)
    print("collecting data for " + screen_name)
    fname = "output/users/{}/user_profile.json".format(screen_name)
    print("Collecting profile information for", screen_name)
    with open(fname, 'a+') as f:
        profile = api.get_user(screen_name=screen_name)        
        f.write(json.dumps(profile._json, indent=3))   
    print("User Profile collected")

getUserProfiles("Adidas")

collecting data for Adidas
User Profile collected


In [122]:
def paginate(items, n):
    for i in range(0, len(items), n):
        yield items[i:i+n]

In [44]:
def getFollowers(screen_name):
    fname = "output/users/{}/followers.json".format(screen_name)
    print("Collecting followers for ", screen_name)
    with open(fname, 'w') as f:
        for followers in Cursor(api.followers_ids, screen_name=screen_name, count=500).pages(2):
            for page in paginate(followers, 100):
                users = api.lookup_users(user_ids=page)
                for user in users:  
                    #print(user.screen_name)
                    f.write(json.dumps(user._json)+"\n")
    print("Followers collected")   
getFollowers("Adidas")

Followers collected


In [45]:
def getFriends(screen_name):
    fname = "output/users/{}/friends.json".format(screen_name)
    print("Collecting friends for ", screen_name)
    with open(fname, 'w') as f:
        for friends in Cursor(api.friends_ids, screen_name=screen_name, count=500).pages(2):
            for page in paginate(friends, 100):
                users = api.lookup_users(user_ids=page)
                for user in users:
                    f.write(json.dumps(user._json)+"\n")
    print("Friends collected")  
getFriends("Adidas")

Friends collected


In [5]:
#Start scraping based on the followers and friends ID
# Loading my authentication tokens
with open('secretsAdidas.json','r') as f:
    twtr_auth = json.load(f)

t = Twitter(auth=OAuth(twtr_auth['token'], twtr_auth['token_secret'], 
            twtr_auth['consumer_key'], twtr_auth['consumer_secret']))

In [124]:
import sys
import time
from twitter.api import TwitterHTTPError
from urllib.error import URLError
from http.client import BadStatusLine

def make_twitter_request(twitter_api_func, max_errors=10, *args, **kw):
    # A nested helper function that handles common HTTPErrors. Return an updated
    # value for wait_period if the problem is a 500 level error. Block until the
    # rate limit is reset if it's a rate limiting issue (429 error). Returns None
    # for 401 and 404 errors, which requires special handling by the caller.
    def handle_twitter_http_error(e, wait_period=2, sleep_when_rate_limited=True):
        if wait_period > 3600: # Seconds
            print('Too many retries. Quitting.', file=sys.stderr)
            raise e
        if e.e.code == 401:
            return None
        elif e.e.code == 404:
            print('Encountered 404 Error (Not Found)', file=sys.stderr)
            return None
        elif e.e.code == 429:
            print('Encountered 429 Error (Rate Limit Exceeded)', file=sys.stderr)
            if sleep_when_rate_limited:
                print("Retrying in 15 minutes...ZzZ...", file=sys.stderr)
                sys.stderr.flush()
                time.sleep(60*15 + 5)
                print('...ZzZ...Awake now and trying again.', file=sys.stderr)
                return 2
            else:
                raise e # Caller must handle the rate limiting issue
        elif e.e.code in (500, 502, 503, 504):
            print('Encountered %i Error. Retrying in %i seconds' % (e.e.code, wait_period), file=sys.stderr)
            time.sleep(wait_period)
            wait_period *= 1.5
            return wait_period
        else:
            raise e

    # End of nested helper function

    wait_period = 2
    error_count = 0
    while True:
        try:
            return twitter_api_func(*args, **kw)
        except TwitterHTTPError as e:
            error_count = 0
            wait_period = handle_twitter_http_error(e, wait_period)
            if wait_period is None:
                return
        except URLError as e:
            error_count += 1
            print("URLError encountered. Continuing.", file=sys.stderr)
            if error_count > max_errors:
                print("Too many consecutive errors...bailing out.", file=sys.stderr)
                raise
        except BadStatusLine as e:
            error_count += 1
            print >> sys.stderr, "BadStatusLine encountered. Continuing."
            if error_count > max_errors:
                print("Too many consecutive errors...bailing out.", file=sys.stderr)
                raise

In [125]:
from functools import partial

def get_friends_followers_ids(twitter_api, screen_name=None, user_id=None,
                                friends_limit=1000, followers_limit=1000):
    # Must have either screen_name or user_id (logical xor)
    assert (screen_name != None) != (user_id != None), \
    "Must have screen_name or user_id, but not both"
    
    #Here we start to collect the 1000 friends and followers from the screen name we given in the array 
    #So we have set the limit 1000 for both the followers and friends retrieve
    get_friends_ids = partial(make_twitter_request, twitter_api.friends.ids,
                                count=1000)
    get_followers_ids = partial(make_twitter_request, twitter_api.followers.ids,
                                count=1000)
    #Here is creating the array to save the followers and friends ids based on the screen name
    friends_ids, followers_ids = [], []
    for twitter_api_func, limit, ids, label in [
            [get_friends_ids, friends_limit, friends_ids, "friends"],
            [get_followers_ids, followers_limit, followers_ids, "followers"]
            ]:
        if limit == 0: continue
        cursor = -1
        #Here is using a while loop to retrieve the ids based on the screen name in the array --
        while cursor != 0:
            if screen_name:
                response = twitter_api_func(screen_name=screen_name, cursor=cursor)
            else: # user_id
                response = twitter_api_func(user_id=user_id, cursor=cursor)
            if response is not None:
                ids += response['ids']
                cursor = response['next_cursor']
            print('Fetched {0} total {1} ids for {2}'.format(len(ids),
                    label, (user_id or screen_name), file=sys.stderr))
            if len(ids) >= limit or response is None:
                break
    return friends_ids[:friends_limit], followers_ids[:followers_limit]

In [126]:
#In this function, the aim is to get the followers count and friends count from the screen name in array 
def get_user_profile(twitter_api, screen_names=None, user_ids=None):
    assert (screen_names != None) != (user_ids != None), \
        "Must have screen_names or user_ids, but not both"
    items_to_info = {}
    items = screen_names or user_ids
    sorted_by_follow_count = []
    while len(items) > 0:
        items_str = ','.join([str(item) for item in items[:100]])
        items = items[100:]
        if screen_names:
            response = make_twitter_request(twitter_api.users.lookup, screen_name=items_str)
        else: # user_ids
            response = make_twitter_request(twitter_api.users.lookup, user_id=items_str)
        for user_info in response:
            if screen_names:
                items_to_info[user_info['followers_count']] = user_info['screen_name']
            else: # user_ids
                items_to_info[user_info['followers_count']] = user_info['id']
    for key in sorted(items_to_info, reverse=True):
        sorted_by_follow_count.append(items_to_info[key])
    return sorted_by_follow_count[:5]

In [127]:
#We ran the dataframe once as we need to create the reciprocalfriend based on the screen anme 
#Run only once to let the system create the dataframe
#df = pd.DataFrame(columns=['ID','ReciprocalFriend'])
#df.to_csv('ReciprocalFriend.csv', index=False)

def save_followers(fid, reciprocal_friend):
    data_frame_rf = [[str(fid), str(i)] for i in reciprocal_friend]
    #print(data_frame_rf)
    df = pd.DataFrame(data_frame_rf, columns=['ID','ReciprocalFriend'])
    with open('ReciprocalFriend.csv', 'a') as f:
        df.to_csv(f,header=False, index=False)

In [129]:
screen_name = "Adidas"
friends_file = 'output/users/{}/friends.json'.format(screen_name)
followers_file = 'output/users/{}/followers.json'.format(screen_name)
user_profile = 'output/users/{}/user_profile.json'.format(screen_name)

users = []
#with open(user_profile) as f:
#        profile = json.loads(line)
#        users.append(profile['screen_name'])
with open(friends_file) as f:
    for line in f:
        profile = json.loads(line)
        users.append(profile['screen_name'])
with open(followers_file) as f:
    for line in f:
        profile = json.loads(line)
        users.append(profile['screen_name'])
print(len(users))

1160


In [128]:
#Here is starting the crawl the followers and friends based on the screen name
def crawl_followers(twitter_api, screen_name, limit=1000000, depth=2):
    
    # Resolve the ID for screen_name and start working with IDs for consistency
    seed_id = str(twitter_api.users.show(screen_name=screen_name)['id'])
    friends_ids, followers_ids = get_friends_followers_ids(twitter_api, user_id=seed_id,
                                 friends_limit=limit, followers_limit=limit)
    rp_friend = list(set(friends_ids) & set(followers_ids))
    top_five = get_user_profile(t, user_ids=rp_friend[:100])
    next_queue = top_five
    
    save_followers(seed_id, next_queue)

In [ ]:
for name in users:
    crawl_followers(t, name, depth=1, limit=1000)

Fetched 705 total friends ids for 17719735
Fetched 1000 total followers ids for 17719735
Fetched 165 total friends ids for 2317310666
Fetched 1000 total followers ids for 2317310666
Fetched 326 total friends ids for 4634443760
Fetched 1000 total followers ids for 4634443760
Fetched 174 total friends ids for 4754087063
Fetched 1000 total followers ids for 4754087063
Fetched 6 total friends ids for 2829449485
Fetched 1000 total followers ids for 2829449485
Fetched 590 total friends ids for 744334658
Fetched 1000 total followers ids for 744334658
Fetched 1000 total friends ids for 267425142
Fetched 1000 total followers ids for 267425142
Fetched 717 total friends ids for 141817380
Fetched 1000 total followers ids for 141817380
Fetched 1 total friends ids for 256573865
Fetched 1000 total followers ids for 256573865
Fetched 57 total friends ids for 348332740
Fetched 1000 total followers ids for 348332740
Fetched 588 total friends ids for 25254853
Fetched 1000 total followers ids for 25254853

Encountered 429 Error (Rate Limit Exceeded)
Retrying in 15 minutes...ZzZ...


In [1]:
#Read the data from the file 
import numpy as np
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt

In [2]:
df = pd.read_csv("ReciprocalFriendAdidas.csv")
df.head()

ID  ReciprocalFriend
0  1.771974e+07         9570452.0
1           NaN               NaN
2  4.634444e+09       133880286.0
3           NaN               NaN
4  4.634444e+09        22705078.0

In [3]:
df = df.dropna()

In [4]:
df = df.applymap(int)

In [5]:
df.head()

ID    ReciprocalFriend
0    17719735             9570452
2  4634443760           133880286
4  4634443760            22705078
6  4634443760  757976000000000000
8    25254853           300114634

In [6]:
# Create Graph from file
x_point = list(df[df.columns[0]].values)
y_point = list(df[df.columns[1]].values)
edges_list = []
for i in range(len(x_point)):
    edges_list.append((x_point[i], y_point[i]))
node_list = set(x_point+y_point)
RG = nx.Graph()
RG.add_nodes_from(node_list)
RG.add_edges_from(edges_list)

In [7]:
# Display some graph information such as number of nodes and edges
print ("Number of Nodes :", RG.number_of_nodes())
print ("Numebr of edges :", RG.number_of_edges())

Number of Nodes : 2392
Numebr of edges : 1963


In [8]:
# Calculate network density
# It shows how the connected nodes to each others.
print("Network Density", nx.density(RG))

Network Density 0.0006864510028549088


In [9]:
print(nx.is_connected(RG))

False


In [10]:
components = nx.connected_components(RG)
largestSubgraph = max(components, key=len)
print(largestSubgraph)
print(len(largestSubgraph))

{1243170000000000000, 1033260000000000000, 767471000000000000, 1016660000000000000, 1365030000000000000, 1347230000000000000, 1049090000000000000, 1250750000000000000, 141664648, 955944000000000000, 1191370000000000000, 1463063815, 498719623, 1355650000000000000, 1075010000000000000, 1901298962, 43192340, 1214660000000000000, 21360280, 1216870000000000000, 1098600000000000000, 826408000000000000, 61798186, 2337186228, 5548212, 712019258, 1933042237, 796622000000000000, 725023000000000000, 532316230, 1553997000, 858636494, 1305970000000000000, 779175000000000000, 225818852, 1377443052, 444389361, 109857527, 14879097, 3362061051, 1434542204}
41


In [11]:
components = nx.connected_components(RG)

In [12]:
#Need to rerun the component 
minSubgraph = min(components, key=len)
print(minSubgraph)
print('len:',len(minSubgraph))
#print(min_subgraph)

{1212450000000000000, 1269640000000000000}
len: 2


In [13]:
person_dict = dict(RG.degree(RG.nodes))
#person_dict
nx.set_node_attributes(RG, name="degree", values=person_dict)

In [14]:
for i in nx.degree(RG):
  if i[1] == 1:
    print(i[0],i[1])

1212450000000000000 1
124272648 1
312778759 1
1351680000000000000 1
6176772 1
1239040000000000000 1
1136574486 1
90570778 1
2704015396 1
42606634 1
229548081 1
901324000000000000 1
48234559 1
532316230 1
2455281736 1
334921801 1
37716042 1
160374857 1
605225037 1
404889680 1
17186899 1
73064535 1
94445656 1
86868062 1
102522977 1
387219554 1
429269092 1
127123557 1
1135000000000000000 1
1012120000000000000 1
335667311 1
19980401 1
22536315 1
1434542204 1
789457000000000000 1
751633000000000000 1
885137000000000000 1
944209000000000000 1
1391992974 1
1720230037 1
4079001753 1
579477657 1
1545093288 1
87269548 1
1192650000000000000 1
17678527 1
1225520000000000000 1
368132300 1
1024850000000000000 1
858636494 1
28188882 1
47956182 1
367313110 1
1151860000000000000 1
89153759 1
1595711712 1
16670949 1
3352723694 1
1246170000000000000 1
404717813 1
1270780000000000000 1
407560441 1
1014370000000000000 1
1323170000000000000 1
1241250000000000000 1
941282000000000000 1
1122530000000000000 1


2245160967 1
3206074373 1
363319311 1
43192340 1
326766614 1
2395115549 1
361812003 1
389730339 1
2316841006 1
582037555 1
2978254899 1
4019703861 1
1258700000000000000 1
163385399 1
3243683913 1
1484279882 1
1576849484 1
957746000000000000 1
2769965139 1
1275220000000000000 1
88354906 1
1217910000000000000 1
4894273636 1
876507242 1
426119276 1
19763309 1
1287610000000000000 1
1308090000000000000 1
2152927346 1
1244670000000000000 1
728945000000000000 1
937649000000000000 1
854385000000000000 1
3047133316 1
128454786 1
1289760000000000000 1
812017000000000000 1
1207840000000000000 1
1304130000000000000 1
1191490000000000000 1
249475216 1
887361684 1
2887012505 1
975098010 1
1357480000000000000 1
1326760000000000000 1
2363052200 1
2695073968 1
74952893 1
44175552 1
3315134668 1
1183570000000000000 1
743370985 1
2856612096 1
882754000000000000 1
1165890000000000000 1
1104450000000000000 1
837378000000000000 1
1196290000000000000 1
1089600000000000000 1
153227523 1
1294400000000000000 1


33602679 1
3236641913 1
759753000000000000 1
916681000000000000 1
916361000000000000 1
869961000000000000 1
878281000000000000 1
1237280000000000000 1
312745095 1
1278240000000000000 1
896905000000000000 1
822793000000000000 1
3197844631 1
1284520000000000000 1
320519342 1
310951086 1
36797620 1
1047837884 1
965168000000000000 1
1116720000000000000 1
1553997000 1
37092558 1
1018450000000000000 1
1151570000000000000 1
1284690000000000000 1
1909644498 1
2750799059 1
974200020 1
2548743378 1
1350260000000000000 1
1231510000000000000 1
211999966 1
3124239591 1
730074000000000000 1
1276890000000000000 1
1211930000000000000 1
1352730000000000000 1
797504000000000000 1
498392326 1
1246050000000000000 1
1313600000000000000 1
400284945 1
1045380000000000000 1
2587942171 1
1356710000000000000 1
578026783 1
748488000000000000 1
1125320000000000000 1
842730000000000000 1
1486642488 1
1322030000000000000 1
1197170000000000000 1
392412498 1
233725267 1
1150100000000000000 1
92544343 1
12812400000000

In [15]:
from operator import itemgetter

In [16]:
# Sort the degrees of nodes
sortedDegrees = sorted(person_dict.items(), key=itemgetter(1), reverse=True)
#sortedDegrees = sorted(person_dict.items(), key=itemgetter(1), reverse=False)

#print(sortedDegrees)

for p in sortedDegrees[:20]:
  print(p)

(1365470000000000000, 20)
(1365580000000000000, 15)
(1365600000000000000, 14)
(1365760000000000000, 13)
(1365710000000000000, 11)
(1365490000000000000, 10)
(1365660000000000000, 10)
(1365450000000000000, 10)
(1365590000000000000, 10)
(1255390000000000000, 10)
(1365780000000000000, 9)
(1365060000000000000, 7)
(1365700000000000000, 7)
(1355210000000000000, 7)
(1365910000000000000, 7)
(1275110000000000000, 6)
(1364390000000000000, 6)
(80200621, 6)
(1365810000000000000, 6)
(1365750000000000000, 6)


In [17]:
# Calculate node betweenness and eigenvector
betweenness_dict = nx.betweenness_centrality(RG)
eigen_dict = nx.eigenvector_centrality(RG, max_iter=200)
nx.set_node_attributes(RG, name="betweenness", values="betweenness_dict")
nx.set_node_attributes(RG, name="eigenvector", values="eigen_dict")

In [18]:
# Sort nodes by key/values e.g. betweenness
sortedBetweenness = sorted(betweenness_dict.items(), key=itemgetter(1), reverse=True)
print("Top 10 nodes by betweenness centrality:")
for p in sortedBetweenness[:10]:
  print(p)


Top 10 nodes by betweenness centrality:
(141664648, 0.0001837434311723356)
(712019258, 0.00017499374397365294)
(1901298962, 0.00011374593358287441)
(1365470000000000000, 0.0001130459586069798)
(1365030000000000000, 0.00010499624638419177)
(1184790000000000000, 0.00010342130268842888)
(1186830000000000000, 9.992142780895583e-05)
(1339500000000000000, 8.784685947477378e-05)
(1170400000000000000, 8.644690952298456e-05)
(300114634, 8.434698459530073e-05)


In [19]:
#First get the top ??? nodes by betweenness as a list
sortedBetweenness = sorted(betweenness_dict.items(), key=itemgetter(1), reverse=True)
topBetweenness = sortedBetweenness[:10]

#Then find and print their degree
for p in topBetweenness:
  print("User ID : ",p[0], "Degree: ", person_dict[p[0]],"Betweenness: ",p[1])

User ID :  141664648 Degree:  4 Betweenness:  0.0001837434311723356
User ID :  712019258 Degree:  5 Betweenness:  0.00017499374397365294
User ID :  1901298962 Degree:  3 Betweenness:  0.00011374593358287441
User ID :  1365470000000000000 Degree:  20 Betweenness:  0.0001130459586069798
User ID :  1365030000000000000 Degree:  5 Betweenness:  0.00010499624638419177
User ID :  1184790000000000000 Degree:  5 Betweenness:  0.00010342130268842888
User ID :  1186830000000000000 Degree:  5 Betweenness:  9.992142780895583e-05
User ID :  1339500000000000000 Degree:  3 Betweenness:  8.784685947477378e-05
User ID :  1170400000000000000 Degree:  2 Betweenness:  8.644690952298456e-05
User ID :  300114634 Degree:  5 Betweenness:  8.434698459530073e-05


In [20]:
import community
import matplotlib.pyplot as plt
import networkx as nx

#community API
#https://perso.crans.org/aynaud/communities/api.html

In [25]:
plt.figure(figsize=(200,150))
#nx.draw_networkx(G, pos=nx.circular_layout(G))
nx.draw_networkx(RG, pos=nx.spring_layout(RG))
plt.show()
plt.savefig('AdidasNetworkGraph.png')

<Figure size 432x288 with 0 Axes>

In [22]:
partition = community.best_partition(RG)
print(partition)

{1006860000000000000: 17, 812198000000000000: 17, 723382000000000000: 1, 1350020000000000000: 2, 1363750000000000000: 3, 1215370000000000000: 4, 1324840000000000000: 5, 226181127: 6, 1212450000000000000: 7, 1177600000000000000: 8, 124272648: 9, 312778759: 10, 1351680000000000000: 11, 6176772: 12, 1239040000000000000: 13, 1136574486: 14, 90570778: 15, 199802913: 16, 2704015396: 14, 3985252392: 17, 42606634: 18, 229548081: 19, 901324000000000000: 20, 48234559: 21, 532316230: 39, 2455281736: 23, 334921801: 24, 37716042: 17, 160374857: 25, 605225037: 26, 404889680: 27, 17186899: 28, 73064535: 29, 94445656: 30, 86868062: 31, 102522977: 25, 387219554: 32, 429269092: 6, 127123557: 33, 1135000000000000000: 34, 1012120000000000000: 35, 335667311: 36, 19980401: 37, 22536315: 38, 1434542204: 39, 789457000000000000: 40, 751633000000000000: 41, 885137000000000000: 12, 944209000000000000: 42, 1391992974: 43, 14975122: 44, 1720230037: 45, 4079001753: 46, 579477657: 47, 1362600000000000000: 48, 154509

In [23]:
modularity = {} # Create a new, empty dictionary
for k,v in partition.items(): # Loop through the community dictionary
    if v not in modularity:
        modularity[v] = [k] # Add a new key for a modularity class the code hasn't seen before
    else:
        modularity[v].append(k) # Append a name to the list for a modularity class the code has already seen

for k,v in modularity.items(): # Loop through the new dictionary
    #if len(v) > 2: # Filter out modularity classes with 2 or fewer nodes
        print('Class '+str(k)+':', v) # Print out the classes and their members

Class 17: [1006860000000000000, 812198000000000000, 3985252392, 37716042, 14836197, 300114634, 135947004, 2478884017, 27092557, 427779786, 30918702, 332278518, 20434358, 28848474, 1108464084, 1219300000000000000, 58807448, 790148316, 98465307, 3981866772, 1044051920, 14571755, 441129326, 25254853, 77290892, 4633001475, 2439995143]
Class 1: [723382000000000000, 1285980817, 954614844, 3243683913, 3055540390, 411449934]
Class 2: [1350020000000000000, 1365060000000000000, 22553274, 209519962, 1238510000000000000, 1315768376, 53840669, 1216150000000000000, 701238762, 1025020000000000000]
Class 3: [1363750000000000000, 1287820000000000000, 1308820000000000000, 1181340000000000000, 1329610000000000000, 1352230000000000000]
Class 4: [1215370000000000000, 2918212191, 2812404403, 389065077, 1164760000000000000, 1281240000000000000]
Class 5: [1324840000000000000, 1266520000000000000, 1297650000000000000]
Class 6: [226181127, 429269092, 236020256, 2884445793, 375917692, 595835400]
Class 7: [121245

In [24]:
#export data into Gephi's gexf format to be visualized using Gephi
nx.write_gexf(RG, 'Adidas.gexf')


<Figure size 432x288 with 0 Axes>